In [ ]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/rsna-monai-packages/monai-0.6.0-202107081903-py3-none-any.whl
/kaggle/input/rsna-monai-packages/einops-0.3.0-py2.py3-none-any.whl
/kaggle/input/monai-v060-deep-learning-in-healthcare-imaging/MONAI-1.0.0/CONTRIBUTING.md
/kaggle/input/monai-v060-deep-learning-in-healthcare-imaging/MONAI-1.0.0/CODE_OF_CONDUCT.md
/kaggle/input/monai-v060-deep-learning-in-healthcare-imaging/MONAI-1.0.0/environment-dev.yml
/kaggle/input/monai-v060-deep-learning-in-healthcare-imaging/MONAI-1.0.0/Dockerfile
/kaggle/input/monai-v060-deep-learning-in-healthcare-imaging/MONAI-1.0.0/.pre-commit-config.yaml
/kaggle/input/monai-v060-deep-learning-in-healthcare-imaging/MONAI-1.0.0/setup.cfg
/kaggle/input/monai-v060-deep-learning-in-healthcare-imaging/MONAI-1.0.0/LICENSE
/kaggle/input/monai-v060-deep-learning-in-healthcare-imaging/MONAI-1.0.0/.gitignore
/kaggle/input/monai-v060-deep-learning-in-healthcare-imaging/MONAI-1.0.0/requirements-dev.txt
/kaggle/input/monai-v060-deep-learning-in-healthcare-imagin

In [2]:
!pip install monai


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 31.6 MB/s eta 0:00:0000:01


In [3]:
import os
import numpy as np
import pandas as pd
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
from sklearn.model_selection import train_test_split
from sklearn.metrics import roc_auc_score
import monai
from tqdm import tqdm
import glob
import cv2
import pydicom

In [4]:
# Hyperparameters
NUM_EPOCHS = 15
BATCH_SIZE = 4  # Adjusted to fit GPU memory
LEARNING_RATE = 1e-4
DEVICE = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [5]:
# Load dataset
train_df = pd.read_csv("../input/rsna-miccai-brain-tumor-radiogenomic-classification/train_labels.csv")
train_df, val_df = train_test_split(train_df, test_size=0.2, stratify=train_df['MGMT_value'], random_state=42)

In [6]:
# Define dataset class
class BrainTumorDataset(Dataset):
    def __init__(self, data, is_train=True):
        self.data = data
        self.is_train = is_train
    
    def __len__(self):
        return len(self.data)
    
    def __getitem__(self, idx):
        row = self.data.iloc[idx]
        case_id = str(row['BraTS21ID']).zfill(5)
        image_path = f"../input/rsna-miccai-brain-tumor-radiogenomic-classification/train/{case_id}/T1wCE/*.dcm"
        image = self.load_dicom_image(image_path)
        target = torch.tensor([row['MGMT_value']], dtype=torch.float32) if self.is_train else torch.tensor([-1.0])
        return image, target
    
    def load_dicom_image(self, path):
        files = sorted(glob.glob(path))[:16]  # Limit to 16 slices per patient
        if not files:
            print(f"Warning: No DICOM images found at {path}")
            return torch.zeros((1, 16, 256, 256), dtype=torch.float32)  # Handle missing images
        images = [pydicom.dcmread(f).pixel_array for f in files]
        images = [cv2.resize(img, (256, 256)) for img in images]
        img3d = np.stack(images, axis=0)  # Stack along depth dimension
        if img3d.max() > img3d.min():
            img3d = (img3d - img3d.min()) / (img3d.max() - img3d.min())  # Normalize
        else:
            img3d = np.zeros_like(img3d)  # Prevent division by zero
        img3d = torch.tensor(img3d, dtype=torch.float32).unsqueeze(0)  # Add channel dimension [C, D, H, W]
        return img3d

In [7]:
# Create data loaders
train_dataset = BrainTumorDataset(train_df, is_train=True)
val_dataset = BrainTumorDataset(val_df, is_train=True)
train_loader = DataLoader(train_dataset, batch_size=BATCH_SIZE, shuffle=True, num_workers=4)
val_loader = DataLoader(val_dataset, batch_size=BATCH_SIZE, shuffle=False, num_workers=4)

In [8]:
# Define model
model = monai.networks.nets.resnet10(spatial_dims=3, n_input_channels=1, num_classes=1).to(DEVICE)
criterion = nn.BCEWithLogitsLoss()
optimizer = optim.Adam(model.parameters(), lr=LEARNING_RATE)
scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=5, gamma=0.5)
scaler = torch.amp.GradScaler()

In [10]:
# Training loop
for epoch in range(NUM_EPOCHS):
    model.train()
    train_loss = 0.0
    for images, targets in tqdm(train_loader):
        images, targets = images.to(DEVICE), targets.to(DEVICE)
        optimizer.zero_grad()
        with torch.amp.autocast(device_type='cuda'):
            outputs = model(images).view(-1)  # Ensure output shape matches target
            loss = criterion(outputs, targets.view(-1))

        scaler.scale(loss).backward()
        scaler.step(optimizer)
        scaler.update()
        train_loss += loss.item()
    scheduler.step()
    
    # Validation
    model.eval()
    val_loss = 0.0
    val_preds, val_targets = [], []
    with torch.no_grad():
        for images, targets in val_loader:
            images, targets = images.to(DEVICE), targets.to(DEVICE)
            outputs = model(images).view(-1)
            loss = criterion(outputs, targets.view(-1))
            val_loss += loss.item()
            val_preds.extend(torch.sigmoid(outputs).cpu().numpy().flatten())  # Ensure 1D list
            val_targets.extend(targets.cpu().numpy().flatten())  # Ensure 1D list
    
    torch.cuda.empty_cache()

100%|██████████| 117/117 [01:03<00:00,  1.85it/s]


In [2]:
# Save model
try:
    torch.save(model.state_dict(), "3d-resnet10_T1wCE_fold0_0.767.pth")
    print("Model saved successfully as 3d-resnet10_T1wCE_fold0_0.767.pth ✅")
except Exception as e:
    print(f"Error saving model: {e}")

Model saved successfully as 3d-resnet10_T1wCE_fold0_0.767.pth ✅
